In [5]:
%pip install pandas
%pip install plotly
%pip install 'SQLAlchemy==1.4.46'
%pip install nbformat

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [6]:
# Imports
import pandas as pd
import sqlalchemy as sql
import matplotlib.pyplot as plt
import plotly.express as px


In [7]:
engine = sql.create_engine("sqlite:///./data/data.sqlite")
groupedBicycleByStation = None
groupedWeatherByCity = None
with engine.connect() as conn:
    startDate = "2021-01-01"
    ## Bicycle
    # Fetch data from the db
    df_cities = pd.read_sql("SELECT * FROM city", conn)
    df_bicycleStation = pd.read_sql("SELECT * FROM bicycle_station", conn)
    df_bicycleCount = pd.read_sql("SELECT * FROM bicycle_count", conn)

    # Form the data
    df_bicycleCount["timestamp"] = pd.to_datetime(
        df_bicycleCount["timestamp"]
    ).dt.tz_convert(None)
    df_bicycleCount["count"] = df_bicycleCount["count"].astype(int)
    df_bicycleCount = df_bicycleCount.loc[df_bicycleCount["timestamp"] >= startDate]

    # Merge the data
    df = df_bicycleCount.merge(
        df_bicycleStation, left_on="bicycle_station_id", right_on="id", how="right"
    ).merge(df_cities, left_on="city_id", right_on="id", how="right")
    df.set_index("timestamp", inplace=True)

    # Group the data by station
    groupedBicycleByStation = df.groupby("bicycle_station_id")

    ## Weather
    # Fetch data from the db
    df_cities = pd.read_sql("SELECT * FROM city", conn)
    df_weatherStation = pd.read_sql("SELECT * FROM weather_station", conn)
    df_weatherEntry = pd.read_sql("SELECT * FROM weather_entry", conn)

    # Form the data
    df_weatherEntry["date"] = pd.to_datetime(df_weatherEntry["date"])
    df_weatherEntry = df_weatherEntry.loc[df_weatherEntry["date"] >= startDate]

    # Merge the data
    df = df_weatherEntry.merge(
        df_weatherStation, left_on="weather_station_id", right_on="id", how="right"
    ).merge(df_cities, left_on="city_id", right_on="id", how="right")
    df.set_index("date", inplace=True)

    # Group the data by station
    groupedWeatherByCity = df.groupby("city_id")

In [8]:
## Creating weekly dfs for each weather station
cityWeatherWeeklies = []
for city, df_cityWeather in groupedWeatherByCity:
    df_cityWeather = df_cityWeather.resample("W").agg(
        {
            "tavg": "mean",
            "tmin": "min",
            "tmax": "max",
            "prcp": "mean",
            "snow": "mean",
            "wdir": "mean",
            "wspd": "mean",
            "wpgt": "mean",
            "pres": "mean",
            "tsun": "mean",
            "name": "first",
            "city_id": "first",
        }
    )
    df_cityWeather.reset_index(inplace=True)
    df_cityWeather["date"] = pd.to_datetime(df_cityWeather["date"])
    cityWeatherWeeklies.append(df_cityWeather)

## Creating weekly dfs for each bicycle counting station
stationBicycleWeeklies = []
for station, df_station in groupedBicycleByStation:
    df_station = df_station.resample("W").agg(
        {
            "count": "sum",
            "bicycle_station_id": "first",
            "name_y": "first",
            "name_x": "first",
            "city_id": "first",
        }
    )
    df_station.reset_index(inplace=True)
    j = 0

    # Matching weather data to station
    for city in cityWeatherWeeklies:
        if df_station["city_id"].iloc[0] == city["city_id"].iloc[0]:
            df_weather_weekly = city
            break
        j += 1
    df_station = df_station.merge(
        cityWeatherWeeklies[j], left_on="timestamp", right_on="date", how="left"
    )
    stationBicycleWeeklies.append(df_station)

In [9]:
def aggWeightedMean(df, column):
	return (df[column] * df["count"]).sum() / df["count"].sum()

df = stationBicycleWeeklies
weatherTypes = ["tavg","tmax","tmin","tsun","pres","prcp","wpgt","snow","wspd"]
stationNames = []
cityNames = []
columns=['station_id']
for weatherType in weatherTypes:
	columns.append(f"{weatherType}_corr")
dfCorr = pd.DataFrame(columns=columns)

for city_df in df:
	stationNames.append(city_df["name_x"].iloc[0])
	cityNames.append(city_df["name_y"].iloc[0])
	new_row = pd.DataFrame({'station_id': [city_df["bicycle_station_id"].iloc[0]]})
	for weatherType in weatherTypes:
		correlation = city_df["count"].corr(city_df[weatherType])
		new_row[f"{weatherType}_corr"] = correlation
	dfCorr = pd.concat([dfCorr, new_row], ignore_index=True)
cityNames = list(dict.fromkeys(cityNames))

fig0 = px.imshow(dfCorr.drop(dfCorr.columns[0], axis=1).T, y=weatherTypes, x=stationNames, color_continuous_scale='RdBu')
fig0.update_xaxes(tickangle=30)
fig0.update_layout(
		title=dict(text="Correlation Between Weather Effects and Bicycle Frequency by Counting Station", font=dict(size=20), automargin=True, yref='paper'),
)
fig0.show()

df = pd.concat(df).merge(dfCorr, left_on="bicycle_station_id", right_on="station_id", how="left")
results = {}
for column in columns[1:]:
	results[column] = df.groupby("city_id_y").apply(aggWeightedMean, column=column)

df = pd.DataFrame(results)
fig1 = px.imshow(df.T, y=weatherTypes, x=cityNames, color_continuous_scale='RdBu')
fig1.update_xaxes(tickangle=30)
fig1.update_layout(
		title=dict(text="Correlation Between Weather Effects and Bicycle Frequency in Cities (Weighted Average)", font=dict(size=20), automargin=True, yref='paper'),
		xaxis_title="",
)
fig1.show()

# TODO: Find most dependent city


In [10]:
df = pd.concat(stationBicycleWeeklies).groupby(["city_id_x", "timestamp"]).agg({"count": "sum", "name_y": "first", "tavg": "first"}).reset_index()
df['count_rel'] = df["count"]
df['count_rel'] = df.groupby('city_id_x')['count_rel'].transform(lambda x: round((x / x.max())*100))
df["count"] = df['count'].apply(lambda x: f"{round((int(x) / 1000), ndigits=2)}k")
df['timestamp'] = df['timestamp'].dt.strftime('%Y-%m-%d')

fig = px.bar(data_frame=df,x="name_y",y=["count_rel","tavg"],animation_frame="timestamp",barmode="group", range_y=[0,100])

for f in fig.frames:
    for t in f.data:
        t.textfont = dict(size=12)
        t.textangle = 0
        t.textposition = "inside"
        t.cliponaxis = False
        t.text = df['count'][df['timestamp']==f.name]

for t in fig.data:
    if t.name=="tavg": 
        t.text = df['tavg']
        t.texttemplate='%{y:.1f}°C'
        t.update(yaxis="y2")
        t.textposition = "outside"
    else:
        t.textfont = dict(size=12)
        t.textangle = 0
        t.textposition = "inside"
        t.cliponaxis = False
        t.text = df['count'][df['timestamp']==f.name]

for f in fig.frames:
    for t in f.data:
        if t.name=="tavg":
            t.text = df['tavg']
            t.texttemplate='%{y:.1f}°C'
            t.update(yaxis="y2")
            t.textposition = "outside"

fig.update_layout(
    height=600,
    title=dict(text="Behavior of Bicycle Frequency and Temperature over Time", font=dict(size=20), automargin=True, yref='paper'),
    yaxis_title="Bicycle Frequency to City Maximum (%)",
    yaxis2=dict(    
        title="Average Temperature (°C)",
        overlaying="y",
        side="right",
        range=[-10, 25],
        showgrid=False,
        ),
    xaxis=dict(
        title="Cities",
        tickangle=10,
    ),
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="right", x=1),
    legend_title="",
    hovermode="x unified",
)
fig.show()
